In [32]:
from cartoframes.auth import set_default_credentials
set_default_credentials('carto_creds.json')

In [33]:
import geopandas as gpd, numpy as np, pandas as pd
nymap = gpd.read_file("./taxi/nyc_cbg_geoms.geojson")
nymap["geoid"] = nymap["geoid"].astype(np.int64)

In [34]:
pred_pickups = pd.read_csv("./files/pred_pickups.csv", index_col = 0)
pickups_per_day_per_block = pd.read_csv("./files/pickups_per_day_per_block.csv", index_col = 0)

In [35]:
pickup_count_map = pd.merge(nymap, pred_pickups["pred_pickups"], left_on = "geoid", right_index = True, how = "right").fillna(0)

In [36]:
dataset = pd.merge(pickup_count_map, pickups_per_day_per_block["total"], left_on = "geoid", right_index = True, how = "left")

In [46]:
dataset.sort_values(by= "total", ascending = False, inplace = True)
dataset["total"] = dataset["total"].astype(np.int64)

In [47]:
dataset["pred_pickups"][:] = np.round(dataset["pred_pickups"].values)
dataset["difference"] = dataset["pred_pickups"] - dataset["total"]

In [83]:
from cartoframes.viz import *

result_map = Map([
    Layer(
        nymap,
        basic_style(
            color = "grey"
        )
    ),
    Layer(
        dataset,
        popup_hover=[
           popup_element("total", "Real pickups")
        ]
        
        ),
    Layer(
        dataset,
        color_continuous_style(
            "pred_pickups",
             range_max = np.quantile(dataset["pred_pickups"].values, 0.90),
             range_min = np.quantile(dataset["pred_pickups"].values, 0.20)

        ),
        popup_hover=[
           popup_element("pred_pickups", "Predicted pickups")
        ],
        legends= color_continuous_legend(
            title="Predicted pickups",
            description='Number of pickups per block group',
            format=',.4r'
            )
        )
    ],
    widget = True
)

In [85]:
result_map.publish('Taxi Pickup', password=None, if_exists='replace')


{'id': '33e60974-6f72-49c5-89d5-e50de658eadb',
 'url': 'https://juanluisrto.carto.com/kuviz/33e60974-6f72-49c5-89d5-e50de658eadb',
 'name': 'Taxi Pickup',
 'privacy': 'public'}

In [88]:
from cartoframes import to_carto
to_carto(dataset, 'Taxi Pickup', if_exists='replace')

Success! Data uploaded to table "taxi_pickup" correctly


'taxi_pickup'

In [84]:
result_map